## Example GPFS Workflow

This notebook aims to give an example GPFS workflow using an early version of the `rc_gpfs` package. This will start with a raw GPFS log file moving through stages for splitting and conversion to parquet using the Python API, although both steps could be done using the built-in CLI as well. Once the parquet dataset is created, it will create the basic `tld` summarized report on file count and storage use. From there, some example plots showing breakdowns of storage used by file age will be created.

~~This notebook assumes being run in a job with at least one GPU, although some options can be changed to use a CPU-only backend. A GPU is recommended for analyzing larger logs, such as for `/data/project`.~~

**Update: Polars is now the backend for the entire package. No GPU is required for processing**

### Suggested Compute Resources

For analyzing a `/data/project` report, I suggest the following resources:

- ntasks = 1
- cpus-per-task = 32
- mem = 64G

### Package and Input Setup

In [ ]:
from pathlib import Path
import re

# Import the three main Python API submodules for analyzing a report
from rc_gpfs import process, policy
from rc_gpfs.report import plotting
import polars as pl

In [ ]:
# File patch setup
log_dir = '/data/rc/gpfs-policy/data/list-policy_data-project_list-path-external_slurm-32856491_2025-04-14T00:00:15'
gpfs_log_root = Path(log_dir)
raw_log = list(gpfs_log_root.joinpath('raw').glob('*.gz'))[0]
acq = re.search(r"\d{4}-\d{2}-\d{2}",log_dir).group()

### Log Preprocessing

This section shows how to use the `policy` module to split the large GPFS log into smaller parts and then convert each part to a separate parquet file for analysis elsewhere. You can specify different filepaths for the outputs of each stage if you want, but it's generally easier to let the functions use the standard log directory structure seen below:

``` text
.
└── log_root/
    ├── raw/
    │   └── raw_log.gz
    ├── chunks/
    │   ├── list-000.gz
    │   ├── list-001.gz
    │   └── ...
    ├── parquet/
    │   ├── list-000.parquet
    │   ├── list-001.parquet
    │   └── ...
    ├── reports/
    └── misc/
```

The directory structure will be automatically created as needed by each function. It's generally easier to not specify output paths for consistency in organization.

#### Split

In [ ]:
# Split raw log
policy.split(log=raw_log)

#### Convert

Opposed to split, it's much faster to submit the parquet conversion as an array job (built into the `cli` submodule), but it's possible to do here via the multiprocessing library as well.

In [ ]:
from multiprocessing import Pool
from rc_gpfs.utils import parse_scontrol

cores,_ = parse_scontrol()
split_files = list(gpfs_log_root.joinpath('chunks').glob('*.gz'))

In [ ]:
with Pool(cores) as pool:
    pool.map(policy.convert,split_files)

### Aggregate

In [ ]:
pq_path = gpfs_log_root.joinpath('parquet')

In [ ]:
df = pl.scan_parquet(pq_path.joinpath('*.parquet'))

In [ ]:
df_agg = process.aggregate_gpfs_dataset(
    df,
    acq = acq,
    time_breakpoints=[30,60,90,180,365],
    time_unit='D',
    time_val='access'
)

### Plotting

In [ ]:
df_agg_grp = (
    df_agg
    .group_by('dt_grp')
    .agg(pl.col('bytes','file_count').sum())
    .sort('dt_grp',descending=True)
)

In [ ]:
exp,unit = plotting.choose_appropriate_storage_unit(df_agg['bytes'])
df_agg_grp = (
    df_agg_grp
    .with_columns((pl.col('bytes')/(1024**exp)).alias(unit))
    .with_columns([
        pl.cum_sum('file_count').alias('file_count_cum'),
        pl.col(unit).cum_sum().alias(f'{unit}_cum'),
    ])
)

In [ ]:
f = plotting.pareto_chart(df_agg_grp,x='dt_grp',y=unit)

In [ ]:
f